# Starting the Analysis

The main data here is the "layout" data, which contains the information about the layout of the track. The goal is to reproduce the following link: https://roadcurvature.com/download-data/using-kml-files/; https://roadcurvature.com/how-it-works/.
The main idea is to calculate the curvature of the track at each point. Thus, relate the curvatura with other data.

First, let's import the necessary libraries and load the data. 

In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import plotly.express as px
import folium

In [2]:
layout_df = pd.read_csv('data/layout/dados_tracado.csv', sep=';', encoding='latin-1')

layout_df.head(10)

concessionaria  ano_do_pnv_snv rodovia_uf tipo_pista    sentido  \
0  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
1  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
2  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
3  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
4  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
5  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
6  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
7  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
8  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   
9  AUTOPISTA FERNÃO DIAS            2007  BR-381/MG  Principal  Crescente   

  tipo_tracado km_m_inicial latitude_inicial longitude_inicial km_m_final  \
0     Tangente      478,200       -19,961207        -44,037393    478,835   
1        Curva      478,836       -19,963726        -44,042863    479,074   
2     Tangente      479,075       -19,964217        -44,044628    479,081   
3        Curva      479,082       -19,964225        -44,044699    479,592   
4     Tangente      479,593       -19,962799        -44,049184    480,042   
5     Tangente      480,115       -19,960379        -44,052486    480,391   
6        Curva      480,392       -19,958911        -44,054626    480,774   
7     Tangente      480,775       -19,958158        -44,058091    481,271   
8        Curva      481,272       -19,958886        -44,063317    481,390   
9     Tangente      481,391       -19,958963        -44,064454    482,318   

  latitude_final longitude_final  
0     -19,963726      -44,042863  
1     -19,964217      -44,044628  
2     -19,964225      -44,044699  
3     -19,962799      -44,049184  
4     -19,960771      -44,051934  
5     -19,958911      -44,054626  
6     -19,958158      -44,058091  
7     -19,958886      -44,063317  
8     -19,958963      -44,064454  
9     -19,958935      -44,073300

This data is only aboout the start and end points of the curvatures. Therefore, we need to get the whole road data.

In [3]:
road_df = pd.read_csv('data/highwayKM/dados_dos_quilometro_principal.csv', sep=';', encoding='latin-1')
road_df.head(10)

concessionaria  ano_do_pnv_snv    rodovia    km_m      sentido  \
0  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22,600  Decrescente   
1  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22,400  Decrescente   
2  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22,200  Decrescente   
3  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22,000  Decrescente   
4  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21,800  Decrescente   
5  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21,600  Decrescente   
6  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21,400  Decrescente   
7  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21,200  Decrescente   
8  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21,000  Decrescente   
9  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  20,800  Decrescente   

     latitude   longitude  
0  -22,999214  -46,518242  
1  -22,997770  -46,517069  
2  -22,996627  -46,515558  
3  -22,995466  -46,514080  
4  -22,994674  -46,512898  
5  -22,993551  -46,511370  
6  -22,992429  -46,509842  
7  -22,991241  -46,508372  
8  -22,989705  -46,507392  
9  -22,989113  -46,507092

In [4]:
road_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 255127 entries, 0 to 255126
Data columns (total 7 columns):
 #   Column          Non-Null Count   Dtype 
---  ------          --------------   ----- 
 0   concessionaria  255127 non-null  object
 1   ano_do_pnv_snv  255127 non-null  int64 
 2   rodovia         255127 non-null  object
 3   km_m            255127 non-null  object
 4   sentido         255127 non-null  object
 5   latitude        255127 non-null  object
 6   longitude       255127 non-null  object
dtypes: int64(1), object(6)
memory usage: 13.6+ MB


Changing the data types.

In [5]:
road_df['km_m'] = road_df['km_m'].str.replace(',', '.').astype(float)
road_df['ano_do_pnv_snv'] = road_df['ano_do_pnv_snv'].astype(int)
road_df['latitude'] = road_df['latitude'].str.replace(',', '.').astype(float)
road_df['longitude'] = road_df['longitude'].str.replace(',', '.').astype(float)

print(road_df.info())
road_df.head(10)

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 255127 entries, 0 to 255126
Data columns (total 7 columns):
 #   Column          Non-Null Count   Dtype  
---  ------          --------------   -----  
 0   concessionaria  255127 non-null  object 
 1   ano_do_pnv_snv  255127 non-null  int64  
 2   rodovia         255127 non-null  object 
 3   km_m            255127 non-null  float64
 4   sentido         255127 non-null  object 
 5   latitude        255127 non-null  float64
 6   longitude       255127 non-null  float64
dtypes: float64(3), int64(1), object(3)
memory usage: 13.6+ MB
None


concessionaria  ano_do_pnv_snv    rodovia  km_m      sentido  \
0  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22.6  Decrescente   
1  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22.4  Decrescente   
2  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22.2  Decrescente   
3  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  22.0  Decrescente   
4  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21.8  Decrescente   
5  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21.6  Decrescente   
6  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21.4  Decrescente   
7  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21.2  Decrescente   
8  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  21.0  Decrescente   
9  AUTOPISTA FERNÃO DIAS            2007  BR-381/SP  20.8  Decrescente   

    latitude  longitude  
0 -22.999214 -46.518242  
1 -22.997770 -46.517069  
2 -22.996627 -46.515558  
3 -22.995466 -46.514080  
4 -22.994674 -46.512898  
5 -22.993551 -46.511370  
6 -22.992429 -46.509842  
7 -22.991241 -46.508372  
8 -22.989705 -46.507392  
9 -22.989113 -46.507092

Now lets put the roads on a map.

In [15]:
map = folium.Map(location=[-15.788497, -47.879873], zoom_start=4)

colors = ['blue', 'red', 'green', 'purple', 'orange', 'darkred', 'lightred', 'beige', 'darkblue', 'darkgreen', 'cadetblue', 'darkpurple', 'pink', 'lightblue', 'lightgreen', 'black']
road = road_df['rodovia'][0]
line_points = []
for index, row in road_df.iterrows():
    if row['rodovia'] != road:
        folium.PolyLine(locations=line_points, tooltip=road, color=colors[np.random.randint(0, len(colors))], weight=5).add_to(map)
        line_points = []
        road = row['rodovia']
    line_points.append((row['latitude'], row['longitude']))


map